In [1]:
from estnltk.wordnet import wn
import sqlite3

pos = [wn.ADJ, wn.ADV, wn.VERB, wn.NOUN]
synsetList=[]

In [2]:

for i in pos:
    tmp = wn.all_synsets(i)
    for j in tmp:
        synsetList.append(j)        

In [153]:
sset_db = 'wordnet/data/all_synsets.db'
relation_db = 'wordnet/data/all_relations.db'

In [17]:
len(synsetList)

65517

In [5]:
end_vrtx = []
start_vrtx = []
start_sset = []
end_sset = []
rel_type = []

#tmpList = synsetList [:100]

In [156]:
def create_connection(db_file):
    """ create a database connection to the SQLite database
        specified by db_file
    :param db_file: database file
    :return: Connection object or None
    """
    try:
        conn = sqlite3.connect(db_file)
        return conn
    except sqlite3.Error as e:
        print("Connection error: [%s]" % e)

    return None

def create_table(conn, create_table_sql ):
    """ create a table from the create_table_sql statement
    :param conn: Connection object
    :param create_table_sql: a CREATE TABLE statement
    :return:
    """
    try:
        c = conn.cursor()
        c.execute(create_table_sql)
    except sqlite3.Error as e:
        print("Connection error while creating table: [%s]" % e)

def sqlTables(databaseLoc):

    sql_create_synset_table = ''' CREATE TABLE IF NOT EXISTS graph_table(

                                        start_vertex INT NOT NULL,
                                        start_synset TEXT NOT NULL,
                                        end_synset TEXT NOT NULL,
                                        end_vertex INT NOT NULL,
                                        relation TEXT NOT NULL
                                                    ); '''
    conn = create_connection(databaseLoc)
    if conn is not None:
        create_table(conn,sql_create_synset_table)
    else:
        print("Error! cannot create db conn.")

def upload_graph_data(graph_db):

    sqlTables(graph_db)
    conn = create_connection(graph_db)
    cursor=conn.cursor()
    with conn:
        for i in range(len(relation_list)):
            start = start_vrtx[i]
            end   = end_vrtx[i]
            tmp = str(synsetsDb[start])
            start_sset = tmp[9:-8]
            tmp   = str(synsetsDb[end])
            end_sset = tmp[9:-8]
            cursor.execute("INSERT INTO relations_graph(start_vertex, start_synset, end_synset, end_vertex, relation) VALUES(?,?,?,?,?)"\
                                                                ,(start, start_sset, end_sset, end, relation_list[i]))
            conn.commit()

In [48]:
 cursor.execute('SELECT synset_id FROM synset_table WHERE synset_word = ? AND POS = ? AND sense = ?',(sset_name,pos,sense))
                row=cursor.fetchall()

IndentationError: unexpected indent (<ipython-input-48-1d47cc6efe98>, line 2)

In [7]:
rsset = synsetList[0]._raw_synset
rsset.variants[0].literal

'hea'

In [139]:
def fetch_id(synset_word,cursor):
    cursor.execute('SELECT synset_id FROM synset_table WHERE synset_word = ?',(synset_word,))
    sset_id = cursor.fetchone()
    
    return sset_id

In [23]:
def fetch_relation(cursor, sset):
    '''
Relations - "has_hyperonym", "has_hyponym", "has_holonym", "has_meronym"
    '''
    relationList = ["has_hyperonym", "has_hyponym", "has_holonym", "has_meronym"]
    sset_word = sset._raw_synset.variants[0].literal
    
    for rel in relationList:
        rel_sset_list = sset.get_related_synsets(rel)
        if sset.get_related_synsets(rel):
            fetch_relation(cursor,sset)
            for rel_sset in rel_sset_list:              
                rel_word = rel_sset._raw_synset.variants[0].literal
                end_vrtx.append( fetch_id(sset_word,curosr))
                start_vrtx.append( fetch_id(rel_word,cursor))

                end_sset.append(sset_word)
                start_sset.append(rel_word)


In [162]:
def fetch_data(db_file):
    
    relationList = ["has_hyperonym", "has_hyponym", "has_holonym", "has_meronym"]
    relation_str = ["hyperonym", "hyponym", "holonym", "meronym"]
    conn = create_connection(db_file)
    cursor = conn.cursor()
    
    with conn:
        for sset in synsetList:
            for rel in relationList:
                i=0
                rel_sset_list = sset.get_related_synsets(rel)
                if sset.get_related_synsets(rel):
                    rel_type.append(relation_str[i])
                    sset_word = sset._raw_synset.variants[0].literal
                    for rel_sset in rel_sset_list:
                        rel_word = rel_sset._raw_synset.variants[0].literal
                        # TODO: remove this part when input database is complete ?
                        #~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
                        end= fetch_id(sset_word,cursor)
                        start= fetch_id(rel_word,cursor)
                        
                        if end is not None:
                            end_vrtx.append(end[0])
                        if start is not None:
                            start_vrtx.append(start[0])
                        #~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~~
                        end_sset.append(sset_word)
                        start_sset.append(rel_word)
                i+=1
                    

In [155]:
def upload_relations(db_file):
    
    sqlTables(db_file)
    conn = create_connection(db_file)
    cursor = conn.cursor()
    
    with conn:
        for i in range(len(start_vrtx)):
            cursor.execute("INSERT INTO graph_table(start_vertex, start_synset, end_synset, end_vertex, relation) VALUES(?,?,?,?,?)"\
                                                            ,(start_vrtx[i], start_sset[i], end_sset[i], end_vrtx[i],rel_type[i]))
            conn.commit()

In [165]:
upload_relations(relation_db)

In [172]:
start_vrtx = []
end_vrtx   = []
end_sset   = []
start_sset = []
rel_type = []
#TODO: gets only hyperonyms - test it.
fetch_data(sset_db)

KeyboardInterrupt: 

In [151]:
start_vrtx

[397,
 375,
 253,
 254,
 251,
 251,
 236,
 227,
 824,
 509,
 508,
 634,
 576,
 576,
 533,
 702,
 884,
 666,
 440,
 694,
 554,
 606,
 853,
 398,
 50,
 636,
 721,
 835,
 159,
 160,
 161,
 610,
 616,
 630,
 742,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 160,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 161,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,
 159,

In [3]:
def synset_name(raw_synset):
    pos = raw_synset.pos
    literal = raw_synset.variants[0].literal
    sense = "%02d"%raw_synset.variants[0].sense
    return '.'.join([literal,pos,sense])

In [137]:
hyperList = []
for sset in synsetList:
    if sset.get_related_synsets("has_hyperonym"):
        var = sset.get_related_synsets("has_hyperonym")[0]
        print(var)
        rsset = var._raw_synset
        name = rsset.variants[0].literal
        print(name)
        
        #print("synset: ", sset)
        #print("hyperonym: ", sset.get_related_synsets("has_hyperonym")[0])

"Synset('vana.a.01')"
vana
"Synset('värviline.a.01')"
värviline
"Synset('värviline.a.01')"
värviline
"Synset('värviline.a.01')"
värviline
"Synset('ahne.a.02')"
ahne
"Synset('ahne.a.02')"
ahne
"Synset('lahke.a.02')"
lahke
"Synset('kade.a.01')"
kade
"Synset('sõltuv.a.01')"
sõltuv
"Synset('kultuurilembene.a.01')"
kultuurilembene
"Synset('rahvuslik.a.01')"
rahvuslik
"Synset('vokaalne.a.03')"
vokaalne
"Synset('rahvuslik.a.01')"
rahvuslik
"Synset('külluslik.a.01')"
külluslik
"Synset('külluslik.a.01')"
külluslik
"Synset('külluslik.a.01')"
külluslik
"Synset('vanuseline.a.01')"
vanuseline
"Synset('seksuaalne.a.02')"
seksuaalne
"Synset('kirjanduslik.a.01')"
kirjanduslik
"Synset('endeline.a.01')"
endeline
"Synset('tihe.a.01')"
tihe
"Synset('haige.a.01')"
haige
"Synset('tõusiklik.a.01')"
tõusiklik
"Synset('rikas.a.02')"
rikas
"Synset('religioosne.a.01')"
religioosne
"Synset('religioosne.a.01')"
religioosne
"Synset('haige.a.01')"
haige
"Synset('värviline.a.01')"
värviline
"Synset('haige.a.01')"
hai

mõtlema
"Synset('mõtlema.v.01')"
mõtlema
"Synset('kavandama.v.01')"
kavandama
"Synset('kindlaks määrama.v.01')"
kindlaks määrama
"Synset('mõtlema.v.01')"
mõtlema
"Synset('tegema.v.06')"
tegema
"Synset('muutma.v.02')"
muutma
"Synset('jätma.v.02')"
jätma
"Synset('andma.v.02')"
andma
"Synset('jätma.v.01')"
jätma
"Synset('kandma.v.09')"
kandma
"Synset('kandma.v.09')"
kandma
"Synset('tegutsema.v.03')"
tegutsema
"Synset('looma.v.02')"
looma
"Synset('looma.v.02')"
looma
"Synset('teatavaks tegema.v.01')"
teatavaks tegema
"Synset('sisse kandma.v.01')"
sisse kandma
"Synset('määrama.v.04')"
määrama
"Synset('pidama.v.01')"
pidama
"Synset('sobima.v.04')"
sobima
"Synset('looma.v.05')"
looma
"Synset('leiduma.v.01')"
leiduma
"Synset('ütlema.v.02')"
ütlema
"Synset('arvestama.v.03')"
arvestama
"Synset('sarnanema.v.01')"
sarnanema
"Synset('näitama.v.03')"
näitama
"Synset('valmistama.v.02')"
valmistama
"Synset('kasutama.v.01')"
kasutama
"Synset('kasvatama.v.04')"
kasvatama
"Synset('soodustama.v.01')"
sood

"Synset('elama.v.02')"
elama
"Synset('sooritama.v.04')"
sooritama
"Synset('panema.v.01')"
panema
"Synset('rikkuma.v.02')"
rikkuma
"Synset('andma.v.02')"
andma
"Synset('imema.v.02')"
imema
"Synset('manustama.v.01')"
manustama
"Synset('tõmbama.v.02')"
tõmbama
"Synset('kogema.v.01')"
kogema
"Synset('jääma.v.04')"
jääma
"Synset('jääma.v.04')"
jääma
"Synset('sobima.v.04')"
sobima
"Synset('liigutama.v.02')"
liigutama
"Synset('levitama.v.01')"
levitama
"Synset('koguma.v.01')"
koguma
"Synset('koondama.v.01')"
koondama
"Synset('vähendama.v.01')"
vähendama
"Synset('vähendama.v.01')"
vähendama
"Synset('arvestama.v.01')"
arvestama
"Synset('sooritama.v.04')"
sooritama
"Synset('käituma.v.01')"
käituma
"Synset('leiduma.v.01')"
leiduma
"Synset('muutuma.v.01')"
muutuma
"Synset('saatma.v.01')"
saatma
"Synset('elama.v.03')"
elama
"Synset('saavutama.v.01')"
saavutama
"Synset('saavutama.v.01')"
saavutama
"Synset('kokku sattuma.v.01')"
kokku sattuma
"Synset('elama.v.03')"
elama
"Synset('elama.v.03')"
elama


"Synset('soodustama.v.01')"
soodustama
"Synset('surema.v.01')"
surema
"Synset('tõstma.v.03')"
tõstma
"Synset('kangestuma.v.01')"
kangestuma
"Synset('kangestuma.v.01')"
kangestuma
"Synset('häälitsema.v.01')"
häälitsema
"Synset('imestama.v.01')"
imestama
"Synset('sooritama.v.04')"
sooritama
"Synset('kauplema.v.02')"
kauplema
"Synset('tugevdama.v.01')"
tugevdama
"Synset('võnkuma.v.01')"
võnkuma
"Synset('tegema.v.06')"
tegema
"Synset('kultiveerima.v.04')"
kultiveerima
"Synset('jääma.v.04')"
jääma
"Synset('keerama.v.02')"
keerama
"Synset('komplitseerima.v.01')"
komplitseerima
"Synset('häälitsema.v.01')"
häälitsema
"Synset('kõlama.v.02')"
kõlama
"Synset('nutma.v.02')"
nutma
"Synset('järgima.v.01')"
järgima
"Synset('viivitama.v.02')"
viivitama
"Synset('valmistama.v.02')"
valmistama
"Synset('rääkima.v.04')"
rääkima
"Synset('kattuma.v.02')"
kattuma
"Synset('asendama.v.01')"
asendama
"Synset('omandama.v.01')"
omandama
"Synset('kehastuma.v.01')"
kehastuma
"Synset('avama.v.02')"
avama
"Synset('kõr

määrima
"Synset('muutma.v.02')"
muutma
"Synset('nutma.v.02')"
nutma
"Synset('kultiveerima.v.04')"
kultiveerima
"Synset('jääma.v.04')"
jääma
"Synset('määrima.v.01')"
määrima
"Synset('sportima.v.01')"
sportima
"Synset('liikuma.v.03')"
liikuma
"Synset('liikuma.v.03')"
liikuma
"Synset('panema.v.01')"
panema
"Synset('lööma.v.02')"
lööma
"Synset('vehkima.v.03')"
vehkima
"Synset('lugema.v.03')"
lugema
"Synset('muutma.v.02')"
muutma
"Synset('muutma.v.02')"
muutma
"Synset('olema.v.08')"
olema
"Synset('kasutama.v.01')"
kasutama
"Synset('otsustama.v.03')"
otsustama
"Synset('värskendama.v.01')"
värskendama
"Synset('parandama.v.02')"
parandama
"Synset('tundeid väljendama.v.01')"
tundeid väljendama
"Synset('väljutama.v.01')"
väljutama
"Synset('vigastama.v.01')"
vigastama
"Synset('sõitma.v.02')"
sõitma
"Synset('karistama.v.01')"
karistama
"Synset('jääma.v.04')"
jääma
"Synset('kirjutama.v.02')"
kirjutama
"Synset('kandma.v.01')"
kandma
"Synset('halvenema.v.01')"
halvenema
"Synset('külmutama.v.01')"
kül

...

kasvaja
"Synset('vedelik.n.01')"
vedelik
"Synset('tõbi.n.01')"
tõbi
"Synset('haiglus.n.01')"
haiglus
"Synset('haiglus.n.01')"
haiglus
"Synset('tõbi.n.01')"
tõbi
"Synset('muutmine.n.01')"
muutmine
"Synset('psüühika häire.n.01')"
psüühika häire
"Synset('ühing.n.01')"
ühing
"Synset('staatus.n.02')"
staatus
"Synset('vajadus.n.02')"
vajadus
"Synset('ebatäiuslikkus.n.01')"
ebatäiuslikkus
"Synset('aine.n.01')"
aine
"Synset('aine.n.01')"
aine
"Synset('sulam.n.02')"
sulam
"Synset('keemiline ühend.n.01')"
keemiline ühend
"Synset('aine.n.01')"
aine
"Synset('aine.n.01')"
aine
"Synset('element.n.02')"
element
"Synset('orgaaniline ühend.n.01')"
orgaaniline ühend
"Synset('põhjus.n.01')"
põhjus
"Synset('aine.n.01')"
aine
"Synset('aine.n.01')"
aine
"Synset('kate.n.01')"
kate
"Synset('lipiidid.n.01')"
lipiidid
"Synset('muutmine.n.01')"
muutmine
"Synset('aine.n.01')"
aine
"Synset('aine.n.01')"
aine
"Synset('aine.n.01')"
aine
"Synset('keemiline ühend.n.01')"
keemiline ühend
"Synset('materjal.n.01')"
mater

"Synset('kunstiinimene.n.01')"
kunstiinimene
"Synset('riigipea.n.01')"
riigipea
"Synset('ülem.n.01')"
ülem
"Synset('liider.n.01')"
liider
"Synset('täiskasvanu.n.01')"
täiskasvanu
"Synset('teenistuja.n.01')"
teenistuja
"Synset('professionaal.n.01')"
professionaal
"Synset('inimene.n.01')"
inimene
"Synset('looduslik fenomen.n.01')"
looduslik fenomen
"Synset('looduslik fenomen.n.01')"
looduslik fenomen
"Synset('rohttaim.n.01')"
rohttaim
"Synset('taim.n.01')"
taim
"Synset('looduslik objekt.n.01')"
looduslik objekt
"Synset('taimeosa.n.01')"
taimeosa
"Synset('abstraktsioon.n.02')"
abstraktsioon
"Synset('objekt.n.01')"
objekt
"Synset('seos.n.02')"
seos
"Synset('tegu.n.02')"
tegu
"Synset('tegu.n.02')"
tegu
"Synset('suhtlus.n.02')"
suhtlus
"Synset('tegu.n.03')"
tegu
"Synset('mittesaavutamine.n.01')"
mittesaavutamine
"Synset('tegu.n.02')"
tegu
"Synset('muutumine.n.01')"
muutumine
"Synset('tegu.n.03')"
tegu
"Synset('seisundimuutus.n.01')"
seisundimuutus
"Synset('alustamine.n.01')"
alustamine
"Syns

alkohol
"Synset('alkohol.n.01')"
alkohol
"Synset('jahu.n.02')"
jahu
"Synset('jahu.n.02')"
jahu
"Synset('pagaritoode.n.01')"
pagaritoode
"Synset('supp.n.01')"
supp
"Synset('supp.n.01')"
supp
"Synset('supp.n.01')"
supp
"Synset('supp.n.01')"
supp
"Synset('supp.n.01')"
supp
"Synset('supp.n.01')"
supp
"Synset('supp.n.01')"
supp
"Synset('alkohol.n.02')"
alkohol
"Synset('alkohol.n.02')"
alkohol
"Synset('alkohol.n.02')"
alkohol
"Synset('narkootikum.n.01')"
narkootikum
"Synset('arstim.n.02')"
arstim
"Synset('antibiootikum.n.01')"
antibiootikum
"Synset('antibiootikum.n.01')"
antibiootikum
"Synset('antibiootikum.n.01')"
antibiootikum
"Synset('ravimisviis.n.01')"
ravimisviis
"Synset('kalju.n.01')"
kalju
"Synset('kompvek.n.01')"
kompvek
"Synset('kompvek.n.01')"
kompvek
"Synset('kompvek.n.01')"
kompvek
"Synset('kompvek.n.01')"
kompvek
"Synset('kompvek.n.01')"
kompvek
"Synset('kook.n.01')"
kook
"Synset('kook.n.01')"
kook
"Synset('palmiksai.n.01')"
palmiksai
"Synset('kook.n.01')"
kook
"Synset('kook.n.

tapmine
"Synset('tapmine.n.01')"
tapmine
"Synset('mõrv.n.01')"
mõrv
"Synset('puhastamine.n.01')"
puhastamine
"Synset('sport.n.01')"
sport
"Synset('sport.n.01')"
sport
"Synset('sport.n.01')"
sport
"Synset('sport.n.01')"
sport
"Synset('mäng.n.01')"
mäng
"Synset('hasartmäng.n.01')"
hasartmäng
"Synset('hasartmäng.n.01')"
hasartmäng
"Synset('kaardimäng.n.01')"
kaardimäng
"Synset('kaardimäng.n.01')"
kaardimäng
"Synset('lauamäng.n.01')"
lauamäng
"Synset('lauamäng.n.01')"
lauamäng
"Synset('lauamäng.n.01')"
lauamäng
"Synset('lauamäng.n.01')"
lauamäng
"Synset('tants.n.01')"
tants
"Synset('standardtants.n.01')"
standardtants
"Synset('kontratants.n.01')"
kontratants
"Synset('kunsttants.n.01')"
kunsttants
"Synset('Ladina-Ameerika tants.n.01')"
Ladina-Ameerika tants
"Synset('muusika.n.01')"
muusika
"Synset('muusika.n.01')"
muusika
"Synset('muusika.n.01')"
muusika
"Synset('muusika.n.01')"
muusika
"Synset('manööver.n.02')"
manööver
"Synset('töö.n.03')"
töö
"Synset('töö.n.03')"
töö
"Synset('kohustus.n.

KeyboardInterrupt: 

In [37]:
'''cycle for relations - hyponym,hypernym, etc.'''   
for sset in synsetList:
        rsset = sset._raw_synset
        #print(sset)
        for relation_candidate in rsset.internalLinks:
            linked_synset = wn.synset(wn._get_key_from_raw_synset(relation_candidate.target_concept))
            relation_candidate.target_concept = linked_synset._raw_synset
            #print(relation_candidate.target_concept)
            #print(linked_synset)
            #print(relation_candidate.name)            
            '''
            sset_literal    =relation_candidate.target_concept.variants[0].literal
            sset_sense      =relation_candidate.target_concept.variants[0].sense
            sset_pos        =rsset.pos
            #[nimi.literal for nimi in rsset.variants ]
            '''

["Synset('vana.a.01')"]
"Synset('antiikne.a.01')"
["Synset('vana.a.01')"]
"Synset('antiikne.a.01')"
["Synset('vana.a.01')"]
"Synset('antiikne.a.01')"
["Synset('vana.a.01')"]
"Synset('antiikne.a.01')"
["Synset('vana.a.01')"]
"Synset('antiikne.a.01')"
["Synset('vana.a.01')"]
"Synset('antiikne.a.01')"
["Synset('vana.a.01')"]
"Synset('antiikne.a.01')"
["Synset('värviline.a.01')"]
"Synset('punane.a.02')"
["Synset('värviline.a.01')"]
"Synset('punane.a.02')"
["Synset('värviline.a.01')"]
"Synset('punane.a.02')"
["Synset('värviline.a.01')"]
"Synset('punane.a.02')"
["Synset('värviline.a.01')"]
"Synset('punane.a.02')"
["Synset('värviline.a.01')"]
"Synset('punane.a.02')"
["Synset('värviline.a.01')"]
"Synset('punane.a.02')"
["Synset('värviline.a.01')"]
"Synset('punane.a.02')"
["Synset('värviline.a.01')"]
"Synset('punane.a.02')"
["Synset('värviline.a.01')"]
"Synset('punane.a.02')"
["Synset('värviline.a.01')"]
"Synset('punane.a.02')"
["Synset('värviline.a.01')"]
"Synset('punane.a.02')"
["Synset('värv

["Synset('roosa.a.01')"]
"Synset('purpurroosa.a.01')"
["Synset('roosa.a.01')"]
"Synset('puuderroosa.a.01')"
["Synset('roosa.a.01')"]
"Synset('spinellroosa.a.01')"
["Synset('värviline.a.01')"]
"Synset('sinine.a.01')"
["Synset('värviline.a.01')"]
"Synset('sinine.a.01')"
["Synset('värviline.a.01')"]
"Synset('sinine.a.01')"
["Synset('värviline.a.01')"]
"Synset('sinine.a.01')"
["Synset('värviline.a.01')"]
"Synset('sinine.a.01')"
["Synset('värviline.a.01')"]
"Synset('sinine.a.01')"
["Synset('värviline.a.01')"]
"Synset('sinine.a.01')"
["Synset('värviline.a.01')"]
"Synset('sinine.a.01')"
["Synset('värviline.a.01')"]
"Synset('sinine.a.01')"
["Synset('värviline.a.01')"]
"Synset('sinine.a.01')"
["Synset('värviline.a.01')"]
"Synset('sinine.a.01')"
["Synset('värviline.a.01')"]
"Synset('sinine.a.01')"
["Synset('värviline.a.01')"]
"Synset('sinine.a.01')"
["Synset('värviline.a.01')"]
"Synset('sinine.a.01')"
["Synset('värviline.a.01')"]
"Synset('sinine.a.01')"
["Synset('värviline.a.01')"]
"Synset('sini

"Synset('rääkima.v.04')"
["Synset('väljendama.v.01')"]
"Synset('rääkima.v.04')"
["Synset('väljendama.v.01')"]
"Synset('rääkima.v.04')"
["Synset('väljendama.v.01')"]
"Synset('rääkima.v.04')"
["Synset('väljendama.v.01')"]
"Synset('rääkima.v.04')"
["Synset('väljendama.v.01')"]
"Synset('rääkima.v.04')"
["Synset('väljendama.v.01')"]
"Synset('rääkima.v.04')"
["Synset('väljendama.v.01')"]
"Synset('rääkima.v.04')"
["Synset('väljendama.v.01')"]
"Synset('rääkima.v.04')"
["Synset('väljendama.v.01')"]
"Synset('rääkima.v.04')"
["Synset('väljendama.v.01')"]
"Synset('rääkima.v.04')"
["Synset('väljendama.v.01')"]
"Synset('rääkima.v.04')"
["Synset('väljendama.v.01')"]
"Synset('rääkima.v.04')"
["Synset('väljendama.v.01')"]
"Synset('rääkima.v.04')"
["Synset('väljendama.v.01')"]
"Synset('rääkima.v.04')"
["Synset('väljendama.v.01')"]
"Synset('rääkima.v.04')"
["Synset('väljendama.v.01')"]
"Synset('rääkima.v.04')"
["Synset('väljendama.v.01')"]
"Synset('rääkima.v.04')"
["Synset('väljendama.v.01')"]
"Synset('r

"Synset('tegema.v.06')"
["Synset('sooritama.v.04')"]
"Synset('tegema.v.06')"
["Synset('sooritama.v.04')"]
"Synset('tegema.v.06')"
["Synset('sooritama.v.04')"]
"Synset('tegema.v.06')"
["Synset('sooritama.v.04')"]
"Synset('tegema.v.06')"
["Synset('valmistama.v.03')"]
"Synset('vormima.v.01')"
["Synset('valmistama.v.03')"]
"Synset('vormima.v.01')"
["Synset('valmistama.v.03')"]
"Synset('vormima.v.01')"
["Synset('valmistama.v.03')"]
"Synset('vormima.v.01')"
["Synset('valmistama.v.03')"]
"Synset('vormima.v.01')"
["Synset('valmistama.v.03')"]
"Synset('vormima.v.01')"
["Synset('valmistama.v.03')"]
"Synset('vormima.v.01')"
["Synset('valmistama.v.03')"]
"Synset('vormima.v.01')"
["Synset('valmistama.v.03')"]
"Synset('vormima.v.01')"
["Synset('valmistama.v.03')"]
"Synset('vormima.v.01')"
["Synset('valmistama.v.03')"]
"Synset('vormima.v.01')"
["Synset('valmistama.v.03')"]
"Synset('vormima.v.01')"
["Synset('valmistama.v.03')"]
"Synset('vormima.v.01')"
["Synset('valmistama.v.03')"]
"Synset('vormima.v.

["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"
["Synset('tegema.v.06')"]
"Synset('kõlama.v.02')"


...

["Synset('ruum.n.04')"]
"Synset('aatrium.n.03')"
["Synset('ruum.n.04')"]
"Synset('aatrium.n.03')"
["Synset('ruum.n.04')"]
"Synset('aatrium.n.03')"
["Synset('ruum.n.04')"]
"Synset('aatrium.n.03')"
["Synset('maja.n.01')"]
"Synset('domus.n.01')"
["Synset('maja.n.01')"]
"Synset('domus.n.01')"
["Synset('maja.n.01')"]
"Synset('domus.n.01')"
["Synset('maja.n.01')"]
"Synset('domus.n.01')"
["Synset('maja.n.01')"]
"Synset('domus.n.01')"
["Synset('maja.n.01')"]
"Synset('domus.n.01')"
["Synset('maja.n.01')"]
"Synset('domus.n.01')"
["Synset('maja.n.01')"]
"Synset('domus.n.01')"
["Synset('maja.n.01')"]
"Synset('domus.n.01')"
["Synset('maja.n.01')"]
"Synset('domus.n.01')"
["Synset('maja.n.01')"]
"Synset('domus.n.01')"
["Synset('maja.n.01')"]
"Synset('domus.n.01')"
["Synset('maja.n.01')"]
"Synset('domus.n.01')"
["Synset('siseõu.n.01')"]
"Synset('peristüül.n.03')"
["Synset('siseõu.n.01')"]
"Synset('peristüül.n.03')"
["Synset('siseõu.n.01')"]
"Synset('peristüül.n.03')"
["Synset('siseõu.n.01')"]
"Synset(

["Synset('plekk.n.01')"]
"Synset('katuseplekk.n.01')"
["Synset('plekk.n.01')"]
"Synset('katuseplekk.n.01')"
["Synset('plekk.n.01')"]
"Synset('katuseplekk.n.01')"
["Synset('kivikatus.n.01')"]
"Synset('betoonkivikatus.n.01')"
["Synset('kivikatus.n.01')"]
"Synset('betoonkivikatus.n.01')"
["Synset('kivikatus.n.01')"]
"Synset('savikivikatus.n.01')"
["Synset('kivikatus.n.01')"]
"Synset('savikivikatus.n.01')"
["Synset('katusekattematerjal.n.01')"]
"Synset('eterniit.n.02')"
["Synset('kemikaal.n.01')"]
"Synset('polümeer.n.01')"
["Synset('kemikaal.n.01')"]
"Synset('polümeer.n.01')"
["Synset('kemikaal.n.01')"]
"Synset('polümeer.n.01')"
["Synset('kemikaal.n.01')"]
"Synset('polümeer.n.01')"
["Synset('kemikaal.n.01')"]
"Synset('polümeer.n.01')"
["Synset('kemikaal.n.01')"]
"Synset('polümeer.n.01')"
["Synset('puitpõrand.n.01')"]
"Synset('laudpõrand.n.01')"
["Synset('puitpõrand.n.01')"]
"Synset('laudpõrand.n.01')"
["Synset('põrand.n.01')"]
"Synset('parkettpõrand.n.01')"
["Synset('põrand.n.01')"]
"Synse

"Synset('kirjutusmasin.n.01')"
["Synset('masin.n.01')"]
"Synset('kirjutusmasin.n.01')"
["Synset('ütlemine.n.02')"]
"Synset('pressimine.n.05')"
["Synset('ütlemine.n.02')"]
"Synset('pressimine.n.05')"
["Synset('ütlemine.n.02')"]
"Synset('pressimine.n.05')"
["Synset('liikumine.n.04')"]
"Synset('eraldumine.n.05')"
["Synset('liikumine.n.04')"]
"Synset('eraldumine.n.05')"
["Synset('liikumine.n.04')"]
"Synset('eraldumine.n.05')"
["Synset('hääl.n.04')"]
"Synset('ahhetamine.n.01')"
["Synset('hääl.n.04')"]
"Synset('ahhetamine.n.01')"
["Synset('hääl.n.04')"]
"Synset('aietamine.n.01')"
["Synset('hääl.n.04')"]
"Synset('aietamine.n.01')"
["Synset('hääl.n.04')"]
"Synset('aietamine.n.01')"
["Synset('operatsioon.n.05')"]
"Synset('amputeerimine.n.01')"
["Synset('operatsioon.n.05')"]
"Synset('amputeerimine.n.01')"
["Synset('operatsioon.n.05')"]
"Synset('amputeerimine.n.01')"
["Synset('operatsioon.n.05')"]
"Synset('amputeerimine.n.01')"
["Synset('trauma.n.01')"]
"Synset('armistumine.n.01')"
["Synset('trau

"Synset('sublimatsioon.n.01')"
["Synset('atmosfäärinähtus.n.01')"]
"Synset('optiline atmosfäärinähtus.n.01')"
["Synset('atmosfäärinähtus.n.01')"]
"Synset('optiline atmosfäärinähtus.n.01')"
["Synset('atmosfäärinähtus.n.01')"]
"Synset('optiline atmosfäärinähtus.n.01')"
["Synset('atmosfäärinähtus.n.01')"]
"Synset('elektriline atmosfäärinähtus.n.01')"
["Synset('atmosfäärinähtus.n.01')"]
"Synset('elektriline atmosfäärinähtus.n.01')"
["Synset('atmosfäärinähtus.n.01')"]
"Synset('elektriline atmosfäärinähtus.n.01')"
["Synset('atmosfäärinähtus.n.01')"]
"Synset('elektriline atmosfäärinähtus.n.01')"
["Synset('optiline atmosfäärinähtus.n.01')"]
"Synset('halo.n.01')"
["Synset('optiline atmosfäärinähtus.n.01')"]
"Synset('halo.n.01')"
["Synset('optiline atmosfäärinähtus.n.01')"]
"Synset('miraaž.n.01')"
["Synset('optiline atmosfäärinähtus.n.01')"]
"Synset('miraaž.n.01')"
["Synset('optiline atmosfäärinähtus.n.01')"]
"Synset('miraaž.n.01')"
["Synset('ilm.n.01')"]
"Synset('põuailm.n.01')"
["Synset('ilm.n

KeyboardInterrupt: 